Install Libraries

In [1]:
import sys
print(sys.executable)
print(sys.version)
!"{sys.executable}" -m pip install bertopic[visualization] sentence-transformers

c:\Users\A128842\AppData\Local\Programs\Python\Python310\python.exe
3.10.1 (tags/v3.10.1:2cd268a, Dec  6 2021, 19:10:37) [MSC v.1929 64 bit (AMD64)]


In [2]:
import sys
print(sys.executable)
print(sys.version)
!"{sys.executable}" -m pip install bertopic[visualization] -q
!"{sys.executable}" -m pip install matplotlib

c:\Users\A128842\AppData\Local\Programs\Python\Python310\python.exe
3.10.1 (tags/v3.10.1:2cd268a, Dec  6 2021, 19:10:37) [MSC v.1929 64 bit (AMD64)]


In [3]:
import pandas as pd
from bertopic import BERTopic
from sentence_transformers import SentenceTransformer
import matplotlib.pyplot as plt

C:\Users\A128842\AppData\Roaming\Python\Python310\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Load Processed Data

In [4]:
# Load the cleaned dataset (replace path if needed)
df = pd.read_csv("../data/processed/final_cleaned_feedback_2.csv")
# Let's preview the first few rows
df.head(15)

Query_Type  Feedback  \
0                                            -  positive   
1                                            -  positive   
2                                            -  positive   
3                                            -  positive   
4                                            -  positive   
5                                            -  positive   
6                                            -  positive   
7        certification validity period inquiry  positive   
8   medical condition and FMLA extension usage  positive   
9                                            -  positive   
10                                           -  positive   
11                                           -  negative   
12                                           -  positive   
13                                           -  positive   
14                                           -  positive   

               Conversation_Topic  Conversation_Subtopic  \
0          Accurate Summarization                    NaN   
1          Accurate Summarization                    NaN   
2          Accurate Summarization                    NaN   
3          Accurate Summarization                    NaN   
4          Accurate Summarization                    NaN   
5          Accurate Summarization                    NaN   
6          Accurate Summarization                    NaN   
7   Credentialing & Certification                    NaN   
8                            FMLA                    NaN   
9          Accurate Summarization                    NaN   
10         Accurate Summarization                    NaN   
11       Inaccurate Summarization                    NaN   
12         Accurate Summarization                    NaN   
13         Accurate Summarization                    NaN   
14         Accurate Summarization                    NaN   

                                     Knowledge_Answer  \
0   status salary advance payment ment hour approv...   
1   status salary advance payment ment hour approv...   
2   status modify payment arrangement document sen...   
3   status modify payment arrangement document sen...   
4   add guardian benefit emergency basis health ca...   
5   salary step increase retirement health benefit...   
6   take leave absence care child disability seek ...   
7   employee * california region documentation lic...   
8   southern california region employee utilize fa...   
9   report thir contribution charles schwab stop d...   
10  seek information fmla leave condition step inc...   
11  hour condition fmla leave option usage cesla h...   
12  update termination date member termination dat...   
13  update termination date member termination dat...   
14  addition health insurance plan document find a...   

                                            Knowledge Agent_ID  \
0                                                   -  S522948   
1                                                   -  S522948   
2                                                   -  S522948   
3                                                   -  S522948   
4                                                   -  S160879   
5                                                   -  S522948   
6                                                   -  S187441   
7   License Certification and Registration LCR 000...  H555395   
8   Medical Leave Initiate GA HI MHS NBU NCAL NW S...  H555395   
9                                                   -  I571881   
10                                                  -  F413251   
11                                                  -  A455645   
12                                                  -  M485482   
13                                                  -  M485482   
14                                                  -  T797917   

              Timestamp Summary_Reason  \
0   2025-05-17 00:58:20              -   
1   2025-05-17 00:58:07              -   
2   2025-05-17 00:

Combine Query And Summary

In [ ]:
# Fill NaN values with empty string to prevent errors during string concatenation
df.replace("-", pd.NA, inplace=True)
df["Summary_Reason"] = df["Summary_Reason"].fillna("")
df["Knowledge_Answer"] = df["Knowledge_Answer"].fillna("")

# Combine Query and Summary into one string for modeling
df["text_input"] = df["Summary_Reason"] + " " + df["Knowledge_Answer"]

# Optional: remove very short entries (e.g., < 5 words) which may be too vague
filtered_df = df[df["text_input"].str.split().str.len() > 5]

# Confirm we have usable data
filtered_df["text_input"].sample(5)

1649      employee region experience issue paycheck ste...
945       open case settlement payment hr connect emplo...
2398      employee colorado benefit * * program offer c...
14877     addition insurance benefit step ensure add * ...
1530      hr service center regard pay discrepancy empl...
Name: text_input, dtype: object

Initialize BERTopic with cusom embedding model

In [6]:
# Load a SentenceTransformer model (can swap later for domain-tuned models)
#embedding_model = SentenceTransformer("all-MiniLM-L6-v2")
embedding_model_complex = SentenceTransformer("BAAI/bge-small-en-v1.5")

Adjust our model knobs to better fit our data

In [8]:
# Import UMAP for dimensionality reduction
from umap import UMAP

# Configure UMAP to preserve more global structure and reduce dimensionality sensibly
umap_model = UMAP(
    n_neighbors=10,    # How many neighbors to consider—higher = more global structure
    n_components=5,    # How many dimensions to reduce to (default is 5)
    min_dist=0.0,      # Minimum distance between points—lower = tighter clusters
    metric="cosine"    # Cosine distance usually works well for embeddings
)

# Import HDBSCAN for clustering
from hdbscan import HDBSCAN

# Configure HDBSCAN to find smaller, denser clusters
hdbscan_model = HDBSCAN(
    min_cluster_size=5,  # Minimum size for a cluster to be formed
    min_samples=1         # Lower = less conservative, more clusters
)

# Finally, create the BERTopic instance with all custom components
topic_model = BERTopic(
    embedding_model=embedding_model_complex,  # SentenceTransformer model
    umap_model=umap_model,            # configured UMAP
    hdbscan_model=hdbscan_model,      # configured HDBSCAN
    verbose=True                      # Print progress messages
)

Fit BERTopic Model

In [9]:
# Fit the model on your text inputs
# topics, probs = topic_model.fit_transform(filtered_df["text_input"].head(1000))
topics, probs = topic_model.fit_transform(filtered_df["text_input"])

# subset = filtered_df.head(1000).copy()
# subset["Topic"] = topics
# subset["Topic_Probability"] = probs

# Save for later use if needed
filtered_df["Topic"] = topics
filtered_df["Topic_Probability"] = probs

# OPTIONAL: filter out low-confidence assignments
min_confidence = 0.25
# Filter documents and topics by confidence
filtered_docs = []
filtered_topics = []

for doc, topic, prob in zip(filtered_df["text_input"], topics, probs):
    if prob >= min_confidence:
        filtered_docs.append(doc)
        filtered_topics.append(topic)

print(filtered_docs)
print(filtered_topics)

2025-07-22 09:15:47,444 - BERTopic - Embedding - Transforming documents to embeddings.
Batches: 100%|██████████| 512/512 [12:47<00:00,  1.50s/it]
2025-07-22 09:28:34,825 - BERTopic - Embedding - Completed ✓
2025-07-22 09:28:34,825 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2025-07-22 09:29:01,190 - BERTopic - Dimensionality - Completed ✓
2025-07-22 09:29:01,190 - BERTopic - Cluster - Start clustering the reduced embeddings
2025-07-22 09:29:01,700 - BERTopic - Cluster - Completed ✓
2025-07-22 09:29:01,700 - BERTopic - Representation - Fine-tuning topics using representation models.
2025-07-22 09:29:02,915 - BERTopic - Representation - Completed ✓


[' status salary advance payment ment hour approve expect may 19th bank account', ' status salary advance payment ment hour approve expect may 19th bank account', ' status modify payment arrangement document send address wage garnishment issue verify profile document status th document reflect system monday update document', ' status modify payment arrangement document send address wage garnishment issue verify profile document status th document reflect system monday update document', ' take leave absence care child disability seek information fmla eligibility use pto possibility work leave period eligibility integration pto edd benefit option work reduce work schedule have manager form support document give instruction apply edd documentation hr', ' employee * california region documentation license certification registration lcr obtain present calendar day employee region timeline vary georgia ga calendar day hawaii hi calendar day mid mas calendar day * po calendar day * california

In [12]:
# reduce the number of topics by merging similar ones
# (e.g., merge down to 40 topics)
# topic_model.reduce_topics(filtered_docs, nr_topics=40)
# OPTIONAL: inspect topic labels
print(topic_model.get_topic_info())

topic_model.reduce_topics(filtered_df["text_input"], nr_topics=60)

print(topic_model.get_topic_info())

2025-07-22 09:40:16,856 - BERTopic - Topic reduction - Reducing number of topics
2025-07-22 09:40:17,019 - BERTopic - Representation - Fine-tuning topics using representation models.


     Topic  Count                                               Name  \
0       -1   3926                  -1_maternity_leave_clarify_family   
1        0     96             0_enrol_enrolling_enrollment_dependent   
2        1     84                    1_cobra_packet_reinstate_equity   
3        2     82                         2_birthdate_ssn_datum_name   
4        3     80                       3_reopen_event_wait_authoria   
..     ...    ...                                                ...   
995    994      5           994_spouse_participant_medicare_security   
996    995      5  995_ka03j000000em5zcac_paperwork_colorado_phys...   
997    996      5                        996_code_xxxx_checking_card   
998    997      5                       997_push_align_data_demotion   
999    998      5   998_recovery_advance_ka03j000000emhyca0_vacation   

                                        Representation  \
0    [maternity, leave, clarify, family, department...   
1    [enrol, enroll

2025-07-22 09:40:17,814 - BERTopic - Representation - Completed ✓
2025-07-22 09:40:17,821 - BERTopic - Topic reduction - Reduced number of topics from 1000 to 60


    Topic  Count                                          Name  \
0      -1   3926                 -1_leave_employee_request_pay   
1       0   4215               0_leave_employee_pay_california   
2       1   1196                   1_form_need_code_assistance   
3       2   1148                     2_fmla_leave_hour_clarify   
4       3    801           3_enrollment_coverage_event_benefit   
5       4    607              4_position_change_transfer_datum   
6       5    494                   5_document_fax_email_upload   
7       6    432                     6_center_service_hr_issue   
8       7    359                    7_claim_disability_edd_std   
9       8    291            8_benefit_plan_enrollment_coverage   
10      9    242               9_discrepancy_paycheck_pay_hour   
11     10    212  10_retirement_vanguard_contribution_fidelity   
12     11    211              11_spouse_certificate_add_upload   
13     12    176             12_deposit_account_recall_payment   
14     13 

Review Top Topics

In [13]:
import pandas as pd

# Remove row display limits
pd.set_option("display.max_rows", None)

# Get the full topic summary DataFrame
topic_info = topic_model.get_topic_info()

# Print it (no truncation)
print(topic_info)

    Topic  Count                                          Name  \
0      -1   3926                 -1_leave_employee_request_pay   
1       0   4215               0_leave_employee_pay_california   
2       1   1196                   1_form_need_code_assistance   
3       2   1148                     2_fmla_leave_hour_clarify   
4       3    801           3_enrollment_coverage_event_benefit   
5       4    607              4_position_change_transfer_datum   
6       5    494                   5_document_fax_email_upload   
7       6    432                     6_center_service_hr_issue   
8       7    359                    7_claim_disability_edd_std   
9       8    291            8_benefit_plan_enrollment_coverage   
10      9    242               9_discrepancy_paycheck_pay_hour   
11     10    212  10_retirement_vanguard_contribution_fidelity   
12     11    211              11_spouse_certificate_add_upload   
13     12    176             12_deposit_account_recall_payment   
14     13 

Populate our Main Dictionary (Filtered_df) with our found topics

In [14]:
filtered_df["topic"] = topics
filtered_df["topic_probability"] = probs

Build Our Dictionary Mapping For Our Database

In [15]:
# Get topic info
topic_info = topic_model.get_topic_info()

# Build mapping {topic_id: topic_name}
topic_to_label = dict(zip(topic_info["Topic"], topic_info["Name"])) 

# print(topic_to_label)
# print(filtered_df["topic"])

# Check the dtype of the topic column
print("Topic column dtype:", filtered_df["topic"].dtype)

# Show example unique topics
print("Example topic values:", filtered_df["topic"].unique()[:10])

# Check one mapping key type
sample_key = list(topic_to_label.keys())[0]
print("Sample key type:", type(sample_key))

unmapped = (
    filtered_df.loc[~filtered_df["topic"].isin(topic_to_label.keys()), "topic"]
    .unique()
)
print("Topic IDs in your data without a mapping:", unmapped)

print(filtered_df["topic_label"].isna().sum())

filtered_df["topic_label"] = filtered_df["topic"].map(topic_to_label)

Topic column dtype: int64
Example topic values: [251 269  -1 226 853 895  63 348 444  91]
Sample key type: <class 'int'>
Topic IDs in your data without a mapping: [251 269 226 853 895  63 348 444  91 130 663 116 176 840 224 760 296 955
 954 650 345 303 172 140 989 217 115 644 156 112 131 288 922 496 339 539
 343 193 382 395 196 495 575 659 166 543 286 351 242 173 241 913 522 949
 347 353  76 266 559 144 280 157 287 641 175 463 420 465 564 232  68 160
 400  67 123  98 476 125 355 218 816 148 971 811 821 809 230  69 284 836
 417 289 122 170 818 835 658 168 244 245 470 879 665 409  74 777 676 342
 304 535 537 518 668 810 185 866 220 100 137 378 302 135 511  93 533 376
 374 577 259 377  94 632 805 349 868 526 120 184 337 521 405 407 456 408
 672 264  71 106 413  59 228 267 414 415 581 584 473 968  78 626 419 268
 478 603 958 786 464 588 275 773 358 627 118  80  82 340 235 108  64 591
 198 143 273 792 364 997 977 346 103 593 793  96 219 979 785 919 912 911
  89 802 366 943 578 113 652 385 1

KeyError: 'topic_label'

In [16]:
print(filtered_df.head(20))

                                       Query_Type  Feedback  \
0                                            <NA>  positive   
1                                            <NA>  positive   
2                                            <NA>  positive   
3                                            <NA>  positive   
4                                            <NA>  positive   
5                                            <NA>  positive   
6                                            <NA>  positive   
7           certification validity period inquiry  positive   
8      medical condition and FMLA extension usage  positive   
9                                            <NA>  positive   
10                                           <NA>  positive   
11                                           <NA>  negative   
12                                           <NA>  positive   
13                                           <NA>  positive   
14                                           <NA>  posi

In [17]:
# Subset has the topic assignments for the first 1000 rows
noise_subset = subset[subset["Topic"] == -1]

# Print them
for idx, row in noise_subset.iterrows():
    print(f"{idx}: {row['text_input']}\n")

NameError: name 'subset' is not defined

Visualize the Topics

In [18]:
# Interactive topic overview
topic_model.visualize_topics()

# Keyword bar chart for a given topic number (e.g., topic 3)
topic_model.visualize_barchart(top_n_topics=10)

# Topic similarity hierarchy
topic_model.visualize_hierarchy()

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'hoverinfo': 'text',
              'marker': {'color': 'rgb(61,153,112)'},
              'mode': 'lines',
              'type': 'scatter',
              'x': {'bdata': 'AAAAAAAAAADj+Xuw/dXnP+P5e7D91ec/AAAAAAAAAAA=', 'dtype': 'f8'},
              'xaxis': 'x',
              'y': {'bdata': 'AAAAAAAAFMAAAAAAAAAUwAAAAAAAAC7AAAAAAAAALsA=', 'dtype': 'f8'},
              'yaxis': 'y'},
             {'hoverinfo': 'text',
              'marker': {'color': 'rgb(255,65,54)'},
              'mode': 'lines',
              'type': 'scatter',
              'x': {'bdata': 'AAAAAAAAAACO0WmEC7DjP47RaYQLsOM/AAAAAAAAAAA=', 'dtype': 'f8'},
              'xaxis': 'x',
              'y': {'bdata': 'AAAAAAAAOcAAAAAAAAA5wAAAAAAAgEHAAAAAAACAQcA=', 'dtype': 'f8'},
              'yaxis': 'y'},
             {'hoverinfo': 'text',
              'marker': {'color': 'rgb(255,65,54)'},
              'mode': 'lines',
              'type': 'scatter',
              'x': {'bdata': 'jtFphAuw4z+crmYpnPHnP5yuZimc8ec/AAAAAAAAAAA=', 'dtype': 'f8'},
              'xaxis': 'x',
              'y': {'bdata': 'AAAAAAAAPsAAAAAAAAA+wAAAAAAAgEbAAAAAAACARsA=', 'dtype': 'f8'},
              'yaxis': 'y'},
             {'hoverinfo': 'text',
              'marker': {'color': 'rgb(0,116,217)'},
              'mode': 'lines',
              'type': 'scatter',
              'x': {'bdata': '4/l7sP3V5z8oAF31DCjxPygAXfUMKPE/nK5mKZzx5z8=', 'dtype': 'f8'},
              'xaxis': 'x',
              'y': {'bdata': 'AAAAAAAAJMAAAAAAAAAkwAAAAAAAwELAAAAAAADAQsA=', 'dtype': 'f8'},
              'yaxis': 'y'},
             {'hoverinfo': 'text',
              'marker': {'color': 'rgb(35,205,205)'},
              'mode': 'lines',
              'type': 'scatter',
              'x': {'bdata': 'AAAAAAAAAAAki9WJOp7pPySL1Yk6nuk/AAAAAAAAAAA=', 'dtype': 'f8'},
              'xaxis': 'x',
              'y': {'bdata': 'AAAAAACAS8AAAAAAAIBLwAAAAAAAQFDAAAAAAABAUMA=', 'dtype': 'f8'},
              'yaxis': 'y'},
             {'hoverinfo': 'text',
              'marker': {'color': 'rgb(35,205,205)'},
              'mode': 'lines',
              'type': 'scatter',
              'x': {'bdata': 'JIvViTqe6T/K3G4PAWXqP8rcbg8BZeo/AAAAAAAAAAA=', 'dtype': 'f8'},
              'xaxis': 'x',
              'y': {'bdata': 'AAAAAAAATsAAAAAAAABOwAAAAAAAwFLAAAAAAADAUsA=', 'dtype': 'f8'},
              'yaxis': 'y'},
             {'hoverinfo': 'text',
              'marker': {'color': 'rgb(133,20,75)'},
              'mode': 'lines',
              'type': 'scatter',
              'x': {'bdata': 'AAAAAAAAAABmPFlsVUzlP2Y8WWxVTOU/AAAAAAAAAAA=', 'dtype': 'f8'},
              'xaxis': 'x',
              'y': {'bdata': 'AAAAAADAV8AAAAAAAMBXwAAAAAAAQFrAAAAAAABAWsA=', 'dtype': 'f8'},
              'yaxis': 'y'},
             {'hoverinfo': 'text',
              'marker': {'color': 'rgb(133,20,75)'},
              'mode': 'lines',
              'type': 'scatter',
              'x': {'bdata': 'AAAAAAAAAADwthOU2+bqP/C2E5Tb5uo/ZjxZbFVM5T8=', 'dtype': 'f8'},
              'xaxis': 'x',
              'y': {'bdata': 'AAAAAABAVcAAAAAAAEBVwAAAAAAAAFnAAAAAAAAAWcA=', 'dtype': 'f8'},
              'yaxis': 'y'},
             {'hoverinfo': 'text',
              'marker': {'color': 'rgb(133,20,75)'},
              'mode': 'lines',
              'type': 'scatter',
              'x': {'bdata': 'AAAAAAAAAACqeiMnscPmP6p6Iyexw+Y/AAAAAAAAAAA=', 'dtype': 'f8'},
              'xaxis': 'x',
              'y': {'bdata': 'AAAAAADAXMAAAAAAAMBcwAAAAAAAQF/AAAAAAABAX8A=', 'dtype': 'f8'},
              'yaxis': 'y'},
             {'hoverinfo': 'text',
              'marker': {'color': 'rgb(133,20,75)'},
              'mode': 'lines',
              'type': 'scatter',
              'x': {'bdata': 'AAAAAAAAAACIL6yz+WvgP4gvrLP5a+A/AAAAAAAAAAA=', 'dtype': 'f8'},
              'xaxis': 'x',
              'y': {'bdata': 'AAAAAADgYMAAAAAAAOBgwAAAAAAAIGLAAAAAAAAgYsA=', 'dtype': 'f8'},
              'yaxis': 'y'},
             {'hoverinfo': 'text',
   

Save our DF

In [21]:


filtered_df.to_csv("../data/processed/with_topics_Jul_22.csv", index=False)

In [23]:
# Get all topics from the model
topic_info = topic_model.get_topic_info()

# Print the 60 topics (excluding the -1 outlier topic)
for topic_num in topic_info["Topic"]:
    if topic_num == -1:
        continue  # Skip outlier topic

    # Get top words for the topic
    keywords = topic_model.get_topic(topic_num)
    keyword_list = [word for word, _ in keywords[:10]]  # Top 10 words

    # Print nicely
    print(f"Topic {topic_num}: {', '.join(keyword_list)}")


Topic 0: leave, employee, pay, california, https, fmla, my, salesforce, kphr, com
Topic 1: form, need, code, assistance, connect, card, promise, status, time, department
Topic 2: fmla, leave, hour, clarify, maternity, eligibility, bonding, document, form, need
Topic 3: enrollment, coverage, event, benefit, cobra, life, dependent, enroll, add, plan
Topic 4: position, change, transfer, datum, job, approval, kp, org, update, hrconnect
Topic 5: document, fax, email, upload, case, employment, verification, method, send, twn
Topic 6: center, service, hr, issue, regard, promise, verify, case, resolve, express
Topic 7: claim, disability, edd, std, metlife, sdi, salary, benefit, term, continuance
Topic 8: benefit, plan, enrollment, coverage, dependent, severance, insurance, enrol, termination, 1st
Topic 9: discrepancy, paycheck, pay, hour, coordinate, integration, report, disability, promise, timekeepe
Topic 10: retirement, vanguard, contribution, fidelity, pension, saving, award, service, plan

Save the Model

In [ ]:
# Save model for later reuse
topic_model.save("../models/bertopic_base_model")

# Save DataFrame with topics
df.to_csv("../data/processed/with_topics.csv", index=False)
